<center><h1>M1 MMAS - Optimisation</h1><h2>TP2 : descente de gradient par rebroussement d'Armijo</h2></center>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from time import time
params = {'tex.usetex': True}

<h2>I - Application à un problème de classification</h2>

In [ ]:
# Paramètres pour générer les données du problème.
t = 2*np.pi*np.random.rand()
u = np.array([np.cos(t), np.sin(t)])
#

On considère donnée une famille de couples $((x_i,y_i))_{0\leq i\leq M-1}$ où pour tout $i$, $x_i$ est un point du plan $\mathbb{R}^2$ et $y_i\in\{-1,1\}$ défini l'appartenance de $x_i$ à une des deux classes représentées par les nombres $-1$ et $1$.

Les couples $((x_i,y_i))_{0\leq i\leq M-1}$ sont une réalisation d'un échantillon de taille $M$ de la variable aléatoire $(X,Y)$ à valeurs dans $\mathbb{R}^2\times\{-1,1\}$, c'est-à-dire une réalisation de $M$ variables aléatoires indépendantes $(X_i,Y_i)$ de même loi que le couple $(X,Y)$.

Une réalisation de la variable $(X,Y)$ est donnée par la fonction $\mbox{genererCouple}$ suivante :

In [ ]:
def genererCouple():
    # renvoie une réalisation de la variable aléatoire (X,Y)
    if np.random.rand() < 0.5:
        x, y = 2.*np.random.randn(2) + 3*u, -1 # bleu
    else:
        x, y = 2.*np.random.randn(2) - 3*u, 1 # rouge
    return [x, y]

La case suivante génère les données fixées du problème $((x_i,y_i))_{0\leq i\leq M-1}$ et les affiches graphiquement. La population de type "-1" (c'est-à-dire les $x_i$ tels que $y_i=-1$) est affichée en bleu et celle de type "1" en rouge. Les $x_i$ sont stockés dans un vecteur $\mbox{xv}$ et les $y_i$ dans un vecteur $\mbox{yv}$.

In [ ]:
M = 1000
xi_list, yi_list = np.zeros((M, 2)), np.zeros(M)
for i in range(M):
    xi_list[i, :], yi_list[i] = genererCouple() # on stocke les données ((x_i, y_i))_i

# affichage
plt.figure(figsize = (6, 6))
for i in range(M):
    if yi_list[i] == 1: # si x_i est de type 1 alors on affiche un point rouge
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "red")
    else:
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "blue")
plt.title(r"Représentation des $x_i$ (bleu quand $y_i=-1$, rouge sinon)")
plt.axis("tight")
plt.show()

L'objectif de ce TP est, à partir des données d'entraînement ci-dessus $((x_i,y_i))_{0\leq i\leq M-1}$, d'apprendre à prédire, sachant uniquement une nouvelle valeur $x\in\mathbb{R}^2$ de $X$, la valeur du $y$ associé (c'est-à-dire la couleur du point $x$).

Pour cela on va déterminer la meilleur droite passant par $(0,0)$ qui sépare les deux populations (rouge et bleu) des données.

Une droite qui passe par $(0,0)$ a pour équation $f(x) = 0$ où $f : x\in\mathbb{R}^2 \mapsto a_0 x_0 + a_1 x_1$ avec $a = (a_0, a_1)\in\mathbb{R}^2$ un vecteur normal de la droite.

L'idée est donc de trouver la meilleure orientation (paramétrée par $a\in\mathbb{R}^2$) des lignes de niveau de $f$ de sorte qu'un $x$ (généré suivant la loi de $X$) qui se situerait dans le demi-plan où $f$ prend des valeurs négatives, respectivement positives, serait associé à la prédiction $-1$ (couleur bleu), respectivement $1$ (couleur rouge), pour $y$.

Pour déterminer cette meilleure orientation $a\in\mathbb{R}^2$, nous allons chercher à résoudre le problème d'optimisation suivant : 
$$
    \min_{a\in\mathbb{R}^2} \ F(a), \quad \mbox{ où } F:a\in\mathbb{R}^2\mapsto \lambda \|a\|_2^2 + \frac1M \sum_{i=0}^{M-1} \log(1 + e^{-y_i (a_0 x_{i,0} + a_1 x_{i,1})}),
$$
où $\lambda > 0$ est un paramètre fixé et les $x_i = (x_{i,0}, x_{i,1})\in\mathbb{R}^2$ et $y_i\in\{-1,1\}$ sont les données du problème. Ici $\log$ représente le logarithme népérien.

<h3>Résolution numérique du problème d'optimisation</h3>

<b>1) Observer et comprendre la fonction $\mbox{F}$ suivante prenant en argument $\mbox{a}$ et représentant la fonction objectif. Le paramètre $\lambda$ est fixé à $0.05$.

In [ ]:
λ = 0.05
def F(a):
    # implémentation vectorialisée du calcul des quantités <xi, a> pour i \in {0,...,M-1}
    y_a = np.dot(xi_list, a)

    L = np.log(1 + np.exp(-yi_list*y_a))
    return λ*np.dot(a, a) + np.sum(L)/M

<b>2) Calculer le gradient et la hessienne de $F$ en $a\in\mathbb{R}^2$. Montrer que $F$ admet un unique minimum global sur $\mathbb{R}^2$.</b>

<b>3) Ecrire en Python une fonction $\mbox{gradF}$ prenant en argument $a\in\mathbb{R}^2$ et renvoyant $\nabla F(a)$.</b>

In [ ]:
# Valider cette case pour vérifier que votre implémentation du gradient de F est correcte
a = np.random.rand(2)
epsilon = 1e-8
print("Cette quantité doit être de l\'ordre de 1e-8 : ", np.linalg.norm(gradF(a) - np.array([(F(a + epsilon*np.array([1,0])) - F(a))/(epsilon), (F(a + epsilon*np.array([0,1])) - F(a))/(epsilon)])))

<b>4) Ecrire en Python une fonction $\mbox{descente_gradient_rebroussement}$ prenant en argument la fonction objectif $f$, son gradient $\mbox{gradf}$, $\mbox{x0}$ (un point de départ), $\alpha$ et $\beta$ (pour la méthode du rebroussement d'Armijo), $\mbox{epsilon}$ (une tolérance), et $\mbox{Niter}$ (un nombre d'itérations maximum); implémentant l'algorithme de la descente de gradient par rebroussement d'Armijo. La fonction renverra la valeur du dernier itéré ainsi que la liste des itérés successifs. On fera attention à évaluer les fonctions $f$ et $\mbox{gradf}$ le moins de fois possible.

On pourra éventuellement implémenter à part une fonction codant la méthode du calcul d'un pas de descente par rebroussement d'Armijo.</b>

<b>5) Illustrer la converge de l'algorithme en utilisant la fonction $\mbox{plt.semilogy}$. (Indication : on utilisera d'abord l'algorithme avec une tolérance faible, par exemple $10^{-8}$, et on utilisera l'approximée obtenu comme limite de référence).</b>

<b>6) De quel type de convergence s'agit-il ? Justifier.</b>

<b>7) Vérifier la trajectoire obtenue via l'algorithme de descente avec les lignes de niveau de $F$.</b>

In [ ]:
# Definition des grilles et evaluation de f
a_list_0 = [a_list[i][0] for i in range(len(a_list))] # on recupère les abscisses des itérés
a_list_1 = [a_list[i][1] for i in range(len(a_list))] # on recupère les ordonnées des itérés
a_0_min, a_0_max = np.min(a_list_0) - .25, np.max(a_list_0) + .25 # on définit les bornes des abscisses pour le graphe
a_1_min, a_1_max = np.min(a_list_1) - .25, np.max(a_list_1) + .25 # on définit les bornes des ordonnées pour le graphe
s = 100
a_0 = np.linspace(a_0_min, a_0_max, s) # grille abscisses
a_1 = np.linspace(a_1_min, a_1_max, s) # grille ordonnées
a_0, a_1 = np.meshgrid(a_0, a_1) # grille abcisses, grille ordonnées -> grille 2D
Z = np.zeros((s, s))
for i in range(s):
    for j in range(s):
        Z[i, j] = F([a_0[i, j], a_1[i, j]]) # valeurs de F sur la grille 2D

# Graphique des lignes de niveaux
fig, ax = plt.subplots(figsize = (6, 6))
CS = ax.contour(a_0, a_1, Z, 25)

plt.plot(a_list_0, a_list_1, marker = "o", ms = 4.0, color = "red")
plt.plot(a_star[0], a_star[1], marker = '*', ms = 15.0, color = "r")
ax.clabel(CS, fontsize = 8)
ax.set_title('Lignes de niveau')
ax.set_aspect('equal', adjustable = 'box')

<b>8) On considère la fonction $\mbox{f}$ suivante, où $\mbox{a_star}$ représente l'approximation de la solution renvoyée par l'algorithme.</b>

In [ ]:
def sigmoid(t):
    return 2/(1 + np.exp(-2*t)) - 1

In [ ]:
def f(x):
    return sigmoid(x[0]*a_star[0] + x[1]*a_star[1])

<b>Interpréter la figure suivante.</b>

In [ ]:
X0 = np.linspace(-11, 11, 100)
X1 = np.linspace(-11, 11, 100)
X0, X1 = np.meshgrid(X0, X1)
Z = f([X0, X1])

# Graphique des lignes de niveaux
fig, ax = plt.subplots(figsize = (6, 6))
CS = ax.contourf(X0, X1, Z, 50, cmap = "copper")
for i in range(M):
    if yi_list[i] == 1:
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "red")
    else:
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "blue")
ax.clabel(CS, fontsize = 8)
ax.set_title(r"Séparation des observations $x_i$ en leurs label $y_i$ par $f$")
ax.set_aspect("equal", adjustable = "box") # pour que les axes aient la même échelle

<h3>II) Application au débruitage d'images</h3>

In [ ]:
def ps(x, y):
    # produit scalaire entre x et y, qui peuvent être des vecteurs ou des matrices.
    return np.sum(x*y)

<b>0) Modifier la fonction codant l'algorithme de descente de gradient par rebroussement de sorte que le critère d'arrêt fasse intervenir la quantité $\frac{\| \nabla F(x)\|}{F(x)}$ plutôt que $\| \nabla F(x)\|$. Pourquoi ce changement est-il pertinent ?</b>

Récupérer l'image à l'adresse : https://qdenoyelle.github.io/M1_Optim/TP/paysage.jpg et la placer dans le dossier où le TP se situe.

In [ ]:
plt.figure(figsize = (8, 6))
img_original = plt.imread("paysage.jpg").astype(float) # chargement de l'image
img_original = sum([img_original[:, :, i] for i in range(2)]) # on transforme l'image en noir et blanc
img_original = 1/(np.max(img_original)-np.min(img_original))*(img_original - np.min(img_original))
plt.imshow(img_original, cmap = 'gray') # affichage de l'image
plt.show()

On va traiter l'image comme une matrice dont les coefficients sont le niveau de gris des pixels.

In [ ]:
n, m = img_original.shape # on récupère le nombre de ligne et de colonnes.
print("Nombre de lignes : ", n)
print("Nombre de colonnes : ", m)

On va maintenant dégrader l'image par un bruit additif gaussien (en pratique on aurait uniquement accès à l'image bruitée, ici on cré "artificiellement" le bruit).

In [ ]:
bruit = .2 * np.random.randn(n, m) # bruit gaussien qui va être appliqué sur l'image
img_bruit = img_original + bruit # on bruite additivement l'image

<b>1) Afficher l'image bruitée.</b>

In [ ]:
plt.figure(figsize = (8, 6))
plt.imshow(img_bruit, cmap = "gray") # affichage de l'image
plt.show()

Dans la suite les images seront vues comme des tableaux de valeurs (chaque pixel est un nombre représentant le niveau de gris), c'est à dire des matrices à $n$ lignes et $m$ colonnes.

On va maintenant chercher à débruiter l'image ci-dessus (i.e. diminuer l'impact du bruit). La méthode adoptée va consister à résoudre le problème d'optimisation suivant
$$
\min_{x\in\mathcal{M}_{n,m}(\mathbb{R})} F(x),
$$
où
$$
F(x) = \frac12 \sum_{i=1}^n\sum_{j=1}^m (x_{i,j} - y_{i,j})^2 + \lambda \sum_{i=1}^{n-1}\sum_{j=1}^m N_\varepsilon(x_{i+1,j} - x_{i,j}) + \lambda \sum_{i=1}^{n}\sum_{j=1}^{m-1} N_\varepsilon(x_{i,j+1} - x_{i,j}).
$$
$y\in\mathcal{M}_{n,m}(\mathbb{R})$ est l'image bruitée (la donnée du problème), $\lambda>0$ une constante et 
$$
\forall t\in\mathbb R, \quad N_\varepsilon(t) = \sqrt{t^2+\varepsilon},
$$
avec $\varepsilon>0$.

In [ ]:
y = img_bruit # on stocke dans y l'image bruitée 

<b>3) Interpréter $F$.</b>

<b>4) Justifier que $F$ est $\mathcal C^\infty$ sur $\mathcal{M}_{n,m}(\mathbb{R})$. Montrer que $F$ est strictement convexe et admet un unique minimum global sur $\mathcal{M}_{n,m}(\mathbb{R})$.</b>

<b>5) Calculer le gradient de $F$. On pourra introduire les matrices $L\in\mathcal{M}_{n-1, n}(\mathbb{R})$ avec des $-1$ sur la diagonale, et des $1$ sur la sur-diagonale, et $C\in\mathcal{M}_{m, m-1}(\mathbb{R})$ la matrice avec des $-1$ sur la diagonale, $1$ sur la sous-diagonale</b>.

<b>6) Implémenter les matrices $L$ et $C$. Implémenter des fonctions $\mbox{L_mult}$ et $\mbox{Lt_mult}$ qui réalisent respectivement l'opération $Lx$ pour $x\in\mathcal{M}_{n, m}(\mathbb{R})$ et $L^Tv$ pour $v\in\mathcal{M}_{n-1, m}(\mathbb{R})$. Puis implémenter des fonctions $\mbox{C_mult}$ et $\mbox{Ct_mult}$ qui réalisent respectivement l'opération $xC$ pour $x\in\mathcal{M}_{n, m}(\mathbb{R})$ et $vC^T$ pour $v\in\mathcal{M}_{n, m-1}(\mathbb{R})$.</b>

<b>7) Ecrire une fonction $\mbox{F}$ qui renvoient pour une matrice $x\in\mathcal{M}_{n, m}(\mathbb{R})$, la valeur $F(x)$ de la fonction objective du problème d'optimisation considéré. On pourra au préalable implémenter des fonctions $\mbox{N_eps}$ et $\mbox{dN_eps}$ représentant respectivement $N_\varepsilon$ et $N_\varepsilon'$. On prendra $\varepsilon = 10^{-5}$.</b>

<b>8) Ecrire la fonction $\mbox{gradF}$ implémentant $\nabla F$.</b>

<b>Vérifier votre implémentation du gradient via le calcul de taux d'accroissement de $\mbox{F}$.</b>

<b>9) Utiliser l'algorithme de descente de gradient par rebroussement d'Armijo pour le résoudre le problème d'optimisation. On prendra pour l'instant $\lambda = 0.2$.</b>

<b>10) Illustrer la convergence de l'algorithme.</b>

<b>11) Afficher l'image reconstruite et la comparée aux autres images. Commenter.</b>